In [1]:
from transformers import pipeline

classifier = pipeline("text-classification",model='bhadresh-savani/distilbert-base-uncased-emotion', return_all_scores=True,)

def emotion_scores(sample):
    emotion=classifier(sample)
    return emotion[0]


/opt/homebrew/lib/python3.11/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
/opt/homebrew/lib/python3.11/site-packages/transformers/pipelines/text_classification.py:105: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(


In [2]:
print(emotion_scores("I am happy"))
print(emotion_scores("I am happy")[0]['score'])

[{'label': 'sadness', 'score': 0.0005438445368781686}, {'label': 'joy', 'score': 0.998437225818634}, {'label': 'love', 'score': 0.00045619261800311506}, {'label': 'anger', 'score': 0.0002622490865178406}, {'label': 'fear', 'score': 0.00014311514678411186}, {'label': 'surprise', 'score': 0.00015750866441521794}]
0.0005438445368781686


In [3]:
with open('corpus.txt', 'r') as file:
  lines = file.readlines()
print(lines)
corpus=[]

for line in lines:
    stripedLine=line.strip()
    corpus.append(stripedLine.split())
corpus


['i stand here i feel empty a class post count link href http mooshilu\n', 'i literally just text tychelle to see if she wants to hang out because reading what i just wrote about my nonexistent social life made me feel so pathetic\n', 'i really feel regretful when hearing that shinae got married to another man oh it s really sad i really hope that alex and shinae can be a couple in real life they re perfect for each other\n', 'i believed it was true love and feel devastated i wanted to settle down and have the whole marriage and kids thing with him\n', 'i feel unimportant so inadequate\n', 'i feel very low already\n', 'i feel horrible they wrote again and again personifying an act they were not the cause of it was their progeny who should be genuflecting at her the wronged woman s feet\n', 'ill just paraphrase i ranted about not being able to trust anybody and being hurt feeling rejected etc\n', 'i feel aching at all times of day\n', 'i feel so dumb when at first run through it all see

[['i',
  'stand',
  'here',
  'i',
  'feel',
  'empty',
  'a',
  'class',
  'post',
  'count',
  'link',
  'href',
  'http',
  'mooshilu'],
 ['i',
  'literally',
  'just',
  'text',
  'tychelle',
  'to',
  'see',
  'if',
  'she',
  'wants',
  'to',
  'hang',
  'out',
  'because',
  'reading',
  'what',
  'i',
  'just',
  'wrote',
  'about',
  'my',
  'nonexistent',
  'social',
  'life',
  'made',
  'me',
  'feel',
  'so',
  'pathetic'],
 ['i',
  'really',
  'feel',
  'regretful',
  'when',
  'hearing',
  'that',
  'shinae',
  'got',
  'married',
  'to',
  'another',
  'man',
  'oh',
  'it',
  's',
  'really',
  'sad',
  'i',
  'really',
  'hope',
  'that',
  'alex',
  'and',
  'shinae',
  'can',
  'be',
  'a',
  'couple',
  'in',
  'real',
  'life',
  'they',
  're',
  'perfect',
  'for',
  'each',
  'other'],
 ['i',
  'believed',
  'it',
  'was',
  'true',
  'love',
  'and',
  'feel',
  'devastated',
  'i',
  'wanted',
  'to',
  'settle',
  'down',
  'and',
  'have',
  'the',
  'whole

In [4]:
s=(emotion_scores("sad sadness"))
s

[{'label': 'sadness', 'score': 0.9869638085365295},
 {'label': 'joy', 'score': 0.0035754696000367403},
 {'label': 'love', 'score': 0.002005618531256914},
 {'label': 'anger', 'score': 0.006006756331771612},
 {'label': 'fear', 'score': 0.000984121928922832},
 {'label': 'surprise', 'score': 0.0004642480344045907}]

In [8]:
from collections import defaultdict
import random
import numpy as np

class BigramLM:
  def __init__(self,corpus):
    self.corpus=corpus
    self.vocab=defaultdict(int)
    self.bigramDict=defaultdict(int)
    self.bgModel=defaultdict(float)
    self.LSmoothbgModel=defaultdict(float)
    self.KnModel=defaultdict(float)
    self.preKey=defaultdict(set)
    self.postKey=defaultdict(set)
    self.preCount=defaultdict(int)
    self.postCount=defaultdict(int)
    self.sadness=defaultdict(defaultdict)
    self.joy=defaultdict(defaultdict)
    self.love=defaultdict(defaultdict)
    self.anger=defaultdict(defaultdict)
    self.fear=defaultdict(defaultdict)
    self.surprise=defaultdict(defaultdict)

  def createVocab(self):
    for line in corpus:
      for i in line:
        self.vocab[i]+=1

  def createBigramDict(self):
    for line in corpus:
      if len(line)<2:
        pass
      n1=len(line)
      for i in range(n1-1):
        bg=line[i]+" "+line[i+1]
        self.bigramDict[bg]+=1
        self.preKey[line[i]].add(line[i+1])
        self.postKey[line[i+1]].add(line[i])
  

  




  def buildLM(self):
    for bg in self.bigramDict:
      self.bgModel[bg]=self.bigramDict[bg]/self.vocab[bg.split()[0]]




  def setCount(self):
    for key in self.preKey:
      self.preCount[key]=len(self.preKey[key])
    for key in self.postKey:
      self.postCount[key]=len(self.postKey[key])



  def laplaceSmoothing(self):
    V = len(self.vocab)
    for bg in self.bigramDict:
      self.LSmoothbgModel[bg] = (self.bigramDict[bg] + 1)/(self.vocab[bg.split()[0]]+V)

  def knAlpha(self,d,  preWord):
    return d*self.preCount[preWord]/self.vocab[preWord]

  def knContinuous(self, word):
    return self.postCount[word]/len(self.bigramDict)



  def KneserNey(self,d):
    self.setCount()
    V = len(self.vocab)
    for bg in self.bigramDict:
      self.KnModel[bg]=max(0 , self.bigramDict[bg]-d)/self.vocab[bg.split()[0]]+self.knAlpha(d,bg.split()[0]  )*self.knContinuous(bg.split()[1])

  
  def bigram_emotion_cal(self):

    for bg in self.bgModel:
      # print(bg)
      # print(bg)
      
      i,j=bg.split(" ")
      score = emotion_scores(j)
      self.sadness[i][j]  = self.bgModel[bg] + score[0]['score']
      self.joy[i][j]      = self.bgModel[bg] + score[1]['score']
      self.love[i][j]     = self.bgModel[bg] + score[2]['score']
      self.anger[i][j]    = self.bgModel[bg] + score[3]['score']
      self.fear[i][j]     = self.bgModel[bg] + score[4]['score']
      self.surprise[i][j] = self.bgModel[bg] + score[5]['score']

  def next_word(self, cw , emotion):
    if emotion=="happy":
      if cw not in self.happy:
        nextWord = '.'
        return nextWord
      wordList = list(self.happy[cw].keys())
      weights =  list(self.happy[cw].values())
      nextWord = random.choices(wordList, weights)[0]
    if emotion=="sadness":
      if cw not in self.sadness:
        nextWord = '.'
        return nextWord
      wordList = list(self.sadness[cw].keys())
      weights =  list(self.sadness[cw].values())
      nextWord = random.choices(wordList, weights)[0]
    if emotion=="love":
      if cw not in self.love:
        nextWord = '.'
        return nextWord
      wordList = list(self.love[cw].keys())
      weights =  list(self.love[cw].values())
      nextWord = random.choices(wordList, weights)[0]
    if emotion=="anger":
      if cw not in self.anger:
        nextWord = '.'
        return nextWord
      wordList = list(self.anger[cw].keys())
      weights =  list(self.anger[cw].values())
      nextWord = random.choices(wordList, weights)[0]
    if emotion=="fear":
      if cw not in self.fear:
        nextWord = '.'
        return nextWord
      wordList = list(self.fear[cw].keys())
      weights =  list(self.fear[cw].values())
      nextWord = random.choices(wordList, weights)[0]
    if emotion=="surprise":
      if cw not in self.surprise:
        nextWord = '.'
        return nextWord
      wordList = list(self.surprise[cw].keys())
      weights =  list(self.surprise[cw].values())
      nextWord = random.choices(wordList, weights)[0]
    if emotion=="joy":
      if cw not in self.joy:
        nextWord = '.'
        return nextWord
      wordList = list(self.joy[cw].keys())
      weights =  list(self.joy[cw].values())
      nextWord = random.choices(wordList, weights)[0]
    
    return nextWord
  

  



  def sentence(self, n, emotion):
    
    story = []
    for i in range(n):
      words = []
      # w=vocab.random()
      w = random.choice(list(self.vocab.keys()))
      words.append('i')
      for i in range(12):
        w = self.next_word(w, emotion)
        print(w)
        if w == '.':
          break
        words.append(w)
      story.append((' '.join(words) + '. ').capitalize())
      print(story)
    return story


  def print_vocabs(self):
    print(self.vocab)
    print(self.bigramDict)
    print(self.bgModel)
    print(self.LSmoothbgModel)
    print(self.KnModel)




Bg=BigramLM(corpus)
Bg.createVocab()
Bg.createBigramDict()
Bg.buildLM()
Bg.laplaceSmoothing()
Bg.KneserNey(0.7)
Bg.print_vocabs()
Bg.bigram_emotion_cal()
print("emotion_scores calculated")


# for i in range(5):

#   next = Bg.next_word(i, Bg.joy)
#   print(next)
#   i = next
# Bg.sentence(10, Bg.joy)







defaultdict(<class 'int'>, {'i': 3789, 'stand': 10, 'here': 37, 'feel': 1637, 'empty': 9, 'a': 916, 'class': 13, 'post': 14, 'count': 4, 'link': 2, 'href': 25, 'http': 30, 'mooshilu': 1, 'literally': 4, 'just': 226, 'text': 3, 'tychelle': 1, 'to': 1340, 'see': 45, 'if': 134, 'she': 72, 'wants': 7, 'hang': 1, 'out': 113, 'because': 183, 'reading': 13, 'what': 125, 'wrote': 4, 'about': 298, 'my': 642, 'nonexistent': 1, 'social': 7, 'life': 96, 'made': 36, 'me': 382, 'so': 366, 'pathetic': 6, 'really': 157, 'regretful': 6, 'when': 228, 'hearing': 4, 'that': 796, 'shinae': 2, 'got': 41, 'married': 4, 'another': 19, 'man': 13, 'oh': 8, 'it': 515, 's': 82, 'sad': 24, 'hope': 20, 'alex': 1, 'and': 1453, 'can': 136, 'be': 275, 'couple': 13, 'in': 509, 'real': 13, 'they': 109, 're': 21, 'perfect': 9, 'for': 387, 'each': 17, 'other': 47, 'believed': 2, 'was': 339, 'true': 8, 'love': 70, 'devastated': 8, 'wanted': 20, 'settle': 3, 'down': 31, 'have': 302, 'the': 1277, 'whole': 14, 'marriage': 1, 

['I like him getting complacent about cambodia as me work like simply to. ',
 'I with tech support back theres always dream of peacefulness her goodness that. ',
 'I. ',
 'I that starts at the blessings as full wp image src http pics. ',
 'I of other books the universe to update you say well i feel. ',
 'I feeling today so f amp ed for more supported and speak but. ',
 'I. ',
 'I babies and socializing without feeling really invigorated by being on to earn. ',
 'I over it wont allow myself insane but the systems and with the. ',
 'I like buy some truly in heaven heaven heaven heaven and its gone. ']

In [ ]:
# def next_word(self, word, emotion):

#     vars = {}  # Get potential bigrams with their probabilities
#     bgrs = self.KnModel.keys()
#     for i in bgrs:
#       if list(i)[0] == word:
#         vars[i] = self.bgModel[i]
#     if vars:
#         # Calculate weighted probabilities for bigrams and emotion scores
#         bg_probs = list(vars.values())  # Probabilities from the bigram model
#         emotion_probs = [emotion[bg] for bg in vars.keys()]  # Emotion scores (joy in this case)

#         # Combine probabilities with desired weights
#         combined_probs = [ 0.2*bg + 0.8 * emo for bg, emo in zip(bg_probs, emotion_probs)]

#         # Normalize combined probabilities to ensure they sum to 1
#         total_prob = sum(combined_probs)
#         normalized_probs = [prob / total_prob for prob in combined_probs]

#         # Use weighted random choice based on combined probabilities
#         return ((random.choices(list(vars.keys()), weights=normalized_probs))[0]).split()[0]

In [9]:
joy_lines=['I like him getting complacent about cambodia as me work like simply to. ',
 'I with tech support back theres always dream of peacefulness her goodness that. ',
 'I. ',
 'I that starts at the blessings as full wp image src http pics. ',
 'I of other books the universe to update you say well i feel. ',
 'I feeling today so f amp ed for more supported and speak but. ',
 'I. ',
 'I babies and socializing without feeling really invigorated by being on to earn. ',
 'I over it wont allow myself insane but the systems and with the. ',
 'I like buy some truly in heaven heaven heaven heaven and its gone. ']


In [15]:
joy_lines=Bg.sentence(50, "joy")
print(joy_lines)
sadness_lines=Bg.sentence(50, "sadness")
print(sadness_lines)
love_lines=Bg.sentence(50, "love")
print(love_lines)
anger_lines=Bg.sentence(50, "anger")
print(anger_lines)
fear_lines=Bg.sentence(50, "fear")
print(fear_lines)
surprise_lines=Bg.sentence(50, "surprise")
print(surprise_lines)


more
passionate
toward
him
feel
vital
to
date
will
def
cure
that
['I more passionate toward him feel vital to date will def cure that. ']
or
dad
growing
up
a
completely
accepted
that
subject
clear
yet
gotten
['I more passionate toward him feel vital to date will def cure that. ', 'I or dad growing up a completely accepted that subject clear yet gotten. ']
teachers
having
something
college
on
something
college
are
still
come
from
seems
['I more passionate toward him feel vital to date will def cure that. ', 'I or dad growing up a completely accepted that subject clear yet gotten. ', 'I teachers having something college on something college are still come from seems. ']
i
wish
that
wont
get
hours
in
that
core
problems
where
to
['I more passionate toward him feel vital to date will def cure that. ', 'I or dad growing up a completely accepted that subject clear yet gotten. ', 'I teachers having something college on something college are still come from seems. ', 'I i wish that wont get hou

In [16]:
def save_lines_to_txt(lines, filename):
    with open(filename, "w") as file:
        for line in lines:
            file.write(line+"\n")
save_lines_to_txt(joy_lines, "gen_joy.txt")

In [18]:
def save_lines_to_txt(lines, filename):
    with open(filename, "w") as file:
        for line in lines:
            file.write(line+"\n")
# joy_lines = Bg.sentence(50, Bg.joy)
save_lines_to_txt(joy_lines, "gen_joy.txt")

# sadness_lines = Bg.sentence(50, Bg.sadness)
save_lines_to_txt(sadness_lines, "gen_sadness.txt")

# love_lines = Bg.sentence(50, Bg.love)
save_lines_to_txt(love_lines, "gen_love.txt")

# anger_lines = Bg.sentence(50, Bg.anger)
save_lines_to_txt(anger_lines, "gen_anger.txt")

# fear_lines = Bg.sentence(50, Bg.fear)
save_lines_to_txt(fear_lines, "gen_fear.txt")

# surprise_lines = Bg.sentence(50, Bg.surprise)
save_lines_to_txt(surprise_lines, "gen_surprise.txt")


In [19]:
import pandas as pd
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.svm import SVC
from sklearn.metrics import classification_report

In [20]:

corpus = pd.read_csv("corpus.txt", header=None)[0]
labels = pd.read_csv("labels.txt", header=None)[0]

vectorizer = TfidfVectorizer()
X_train = vectorizer.fit_transform(corpus)

param_grid = {
   "C": [0.1, 1, 10],
   "kernel": ["linear", "rbf", "poly"],
   "gamma": ["scale", "auto"],
}

model = SVC()
grid_search = GridSearchCV(model, param_grid, cv=5)
grid_search.fit(X_train, labels)

best_model = grid_search.best_estimator_



In [22]:
test_data = pd.read_csv("gen_joy.txt", header=None)[0]

X_test = vectorizer.transform(test_data)

predictions = best_model.predict(X_test)
test_labels = np.array(['joy'] * 50) 

accuracy = best_model.score(X_test, test_labels)
print("Accuracy:", accuracy)


Accuracy: 0.46


In [23]:
test_data = pd.read_csv("gen_sadness.txt", header=None)[0]

X_test = vectorizer.transform(test_data)

predictions = best_model.predict(X_test)
test_labels = np.array(['sadness'] * 50) 

accuracy = best_model.score(X_test, test_labels)
print("Accuracy:", accuracy)


Accuracy: 0.62


In [24]:
test_data = pd.read_csv("gen_love.txt", header=None)[0]

X_test = vectorizer.transform(test_data)

predictions = best_model.predict(X_test)
test_labels = np.array(['love'] * 50) 

accuracy = best_model.score(X_test, test_labels)
print("Accuracy:", accuracy)


Accuracy: 0.68


In [25]:
test_data = pd.read_csv("gen_anger.txt", header=None)[0]

X_test = vectorizer.transform(test_data)

predictions = best_model.predict(X_test)
test_labels = np.array(['anger'] * 50) 

accuracy = best_model.score(X_test, test_labels)
print("Accuracy:", accuracy)


Accuracy: 0.38


In [26]:
test_data = pd.read_csv("gen_fear.txt", header=None)[0]

X_test = vectorizer.transform(test_data)

predictions = best_model.predict(X_test)
test_labels = np.array(['fear'] * 50) 

accuracy = best_model.score(X_test, test_labels)
print("Accuracy:", accuracy)


Accuracy: 0.38


In [27]:
test_data = pd.read_csv("gen_surprise.txt", header=None)[0]

X_test = vectorizer.transform(test_data)

predictions = best_model.predict(X_test)
test_labels = np.array(['surprise'] * 50) 

accuracy = best_model.score(X_test, test_labels)
print("Accuracy:", accuracy)


Accuracy: 0.72
